In [1]:
import pandas as pd
from pymedtermino.snomedct import *
from pymedtermino import *


In [2]:
df = pd.read_csv("metamap_output.csv")
df

preferred_name       cui semtypes  score
0   Anterior portion of neck  C0230069   [blor]   5.18
1                       Nose  C0028429   [bpoc]   5.18
2                   Patients  C0030705   [podg]   5.18
3       Pharyngeal structure  C0031354   [bpoc]   5.18
4                     Throat  C3665375   [bpoc]   5.18
5           Etiology aspects  C0015127   [ftcn]   3.98
6        Science of Etiology  C1524003   [cnce]   3.98
7            Acute sinusitis  C0149512   [dsyn]   3.64
8            Mucus discharge  C0333273   [bdsu]   3.60
9                   Treating  C1522326   [ftcn]   3.57
10                     Thick  C1280412   [qlco]   3.43

In [3]:
pref_name=df['preferred_name'].to_list()
pref_name

['Anterior portion of neck',
 'Nose',
 'Patients',
 'Pharyngeal structure',
 'Throat',
 'Etiology aspects',
 'Science of Etiology',
 'Acute sinusitis',
 'Mucus discharge',
 'Treating',
 'Thick']

In [4]:
data = {
    'aapp': 'substance',
    'amas': 'substance',
    'anst': 'body structure - physical object',
    'bact': 'organism - procedure - substance - disorder ',
    'bdsu': 'substance',
    'bdsy': 'body structure',
    'biof': 'observable entity - disorder',
    'blor': 'body structure',
    'bpoc': 'body structure',
    'bsoj': 'body structure',
    'cell': 'Cell',
    'cgab': 'morphologic abnormality - disorder',
    'clna': 'attribute',
    'comd': 'disorder',
    'crbs': 'finding',
    'emst': 'body structure',
    'euka': 'organism',
    'evnt': 'Event',
    'fndg': 'Finding',
    'genf': 'observable entity - disorder',
    "ocdi": "Occupation",
    "orch": "event-procedure - substance",
    "orga": "attribute",
    "orgm": "Organism",    
    "phsu": "substance",
    "sbst": "Substance",
    "spco": "qualifier value",
    "tmco": "qualifier value",
    "topp": "procedure",
}

In [5]:
sems=df['semtypes'].to_list()

x = []
for item in sems:
    if isinstance(item, str):
        item=item[1:-1]
    x.append(item)
    

for index in range(len(x)):
    if isinstance(x[index], str):
        x[index]=x[index].split()
x

[['blor'],
 ['bpoc'],
 ['podg'],
 ['bpoc'],
 ['bpoc'],
 ['ftcn'],
 ['cnce'],
 ['dsyn'],
 ['bdsu'],
 ['ftcn'],
 ['qlco']]

In [6]:
for items in range(len(x)):
    if isinstance(x[items],list):
        for index in range(len(x[items])):
            if x[items][index] in data: 
                x[items][index]=data[x[items][index]]
            else:
                x[items][index]=""
semtype=[]                
for i in range(len(x)):
    for j in range(len(x[i])):
        semtype.append(x[i][j].split(" - "))
semtype

[['body structure'],
 ['body structure'],
 [''],
 ['body structure'],
 ['body structure'],
 [''],
 [''],
 [''],
 ['substance'],
 [''],
 ['']]

In [7]:
concepts={}
for index in range(len(pref_name)):
    for sem in semtype[index]:
        name=f'{pref_name[index]} ({sem})'
        concept = SNOMEDCT.search(name)
        concepts[name]=concept

#         terms = concept.terms()
#         print(terms)
concepts

{'Anterior portion of neck (body structure)': [SNOMEDCT[157054009]  # Entire subcutaneous tissue of anterior portion of neck (body structure),
  SNOMEDCT[181482005]  # Entire skin of anterior portion of neck (body structure),
  SNOMEDCT[11584001]  # Skin structure of anterior portion of neck (body structure),
  SNOMEDCT[362649006]  # Entire anterior portion of neck (body structure),
  SNOMEDCT[49928004]  # Structure of anterior portion of neck (body structure),
  SNOMEDCT[5751008]  # Subcutaneous tissue structure of anterior portion of neck (body structure)],
 'Nose (body structure)': [SNOMEDCT[142006001]  # Entire skeletal muscle of tongue, palate, pharynx AND/OR nose (body structure),
  SNOMEDCT[181195007]  # Entire nose (body structure),
  SNOMEDCT[181201004]  # [SO]Specified nose NEC (body structure),
  SNOMEDCT[181202006]  # Nose NEC (body structure),
  SNOMEDCT[182324007]  # Nose region (body structure),
  SNOMEDCT[110546002]  # Nose and nasopharynx (combined site) (body structur

In [8]:
concept_list=[]
for keys in concepts:
    if len(concepts[keys]):
        if isinstance(concepts[keys],list):
            for i in concepts[keys]:
                concept_list.append(i)
concept_list

[SNOMEDCT[157054009]  # Entire subcutaneous tissue of anterior portion of neck (body structure),
 SNOMEDCT[181482005]  # Entire skin of anterior portion of neck (body structure),
 SNOMEDCT[11584001]  # Skin structure of anterior portion of neck (body structure),
 SNOMEDCT[362649006]  # Entire anterior portion of neck (body structure),
 SNOMEDCT[49928004]  # Structure of anterior portion of neck (body structure),
 SNOMEDCT[5751008]  # Subcutaneous tissue structure of anterior portion of neck (body structure),
 SNOMEDCT[142006001]  # Entire skeletal muscle of tongue, palate, pharynx AND/OR nose (body structure),
 SNOMEDCT[181195007]  # Entire nose (body structure),
 SNOMEDCT[181201004]  # [SO]Specified nose NEC (body structure),
 SNOMEDCT[181202006]  # Nose NEC (body structure),
 SNOMEDCT[182324007]  # Nose region (body structure),
 SNOMEDCT[110546002]  # Nose and nasopharynx (combined site) (body structure),
 SNOMEDCT[110706005]  # Lacrimal sac and nose (combined site) (body structure),

In [9]:
def get_ancestors(concept, visited=None):
    if visited is None:
        visited = set()
    ancestors = []
    for parent in concept.parents:
        if parent in visited:
            continue
        visited.add(parent)
        ancestors.append(parent)
        ancestors.extend(get_ancestors(parent, visited))
    return ancestors

def get_descendants(concept, visited=None):
    if visited is None:
        visited = set()
    descendants = []
    for child in concept.children:
        if child in visited:
            continue
        visited.add(child)
        descendants.append(child)
        descendants.extend(get_descendants(child, visited))
    return descendants


In [10]:
for concept in concept_list:
    try:
        parents = [x for x in concept.parents]
        ancestors = get_ancestors(concept)
        children = [x for x in concept.children]
        descendants = get_descendants(concept)
        groups = concept.groups
        relations = [concept.groups[x].relations for x in range(len(concept.groups))]
        out_of_group = concept.out_of_group
        
        if concept.is_in_core:
            core = True
        else:
            core = False
        
        #     finding_site = [concept.groups[x].finding_site for x in range(len(concept.groups))]
        #     associated_morphology = [concept.groups[x].associated_morphology for x in range(len(concept.groups))]
        
        print(f"Concept: {concept}")
        print(f"Concept Code: {concept.code}\n")
        print(f"Concept Name: {concept.term}\n")
        print(f"Concept Synonyms: {concept.terms}\n")
        print(f"Concept Parents: {parents}\n")
        print(f"Concept Ancestors: {ancestors}\n")
        print(f"Concept Children: {children}\n")
        print(f"Concept Descendants: {descendants}\n")
        print(f"Concept is Sub-part of: {concept.part_of}\n")
        print(f"Concept is Super-part of: {concept.INVERSE_part_of}\n")
        print(f"All Super-parts of Concept: {list(concept.ancestor_parts())}\n")
        print(f"All Sub-parts of Concept: {list(concept.descendant_parts())}\n")
        print(f"concept.relations: {concept.relations}\n")
        print(f"concept.groups: {groups}\n")
        print(f"concept.groups.relations: {relations}\n")
        print(f"concept.out_of_group: {out_of_group}\n")
        print(f"concept in core list: {core}\n")
        print("\n\n\n")
    
    except Exception as e:
        continue

Concept: SNOMEDCT[157054009]  # Entire subcutaneous tissue of anterior portion of neck (body structure)

Concept Code: 157054009

Concept Name: Entire subcutaneous tissue of anterior portion of neck (body structure)

Concept Synonyms: ['Entire subcutaneous tissue of anterior portion of neck', 'Subcutaneous tissue of anterior portion of neck', 'Entire subcutaneous tissue of anterior portion of neck (body structure)']

Concept Parents: [SNOMEDCT[5751008]  # Subcutaneous tissue structure of anterior portion of neck (body structure)
]

Concept Ancestors: [SNOMEDCT[5751008]  # Subcutaneous tissue structure of anterior portion of neck (body structure)
, SNOMEDCT[81853001]  # Subcutaneous tissue structure of neck (body structure)
, SNOMEDCT[127961008]  # Soft tissues of neck (body structure)
, SNOMEDCT[45048000]  # Neck structure (body structure)
, SNOMEDCT[303340002]  # Face and neck structure (body structure)
, SNOMEDCT[774007]  # Head and neck structure (body structure)
, SNOMEDCT[70104002

Concept: SNOMEDCT[385383008]  # Ear, nose and throat structure (body structure)

Concept Code: 385383008

Concept Name: Ear, nose and throat structure (body structure)

Concept Synonyms: ['Ear, nose and throat structure (body structure)', 'Ear, nose and throat structure', 'Ear, nose and throat', 'Structure of ear, nose, and/or throat', 'Structure of ear, nose, and/or throat (body structure)', 'Ear, nose and/or throat']

Concept Parents: [SNOMEDCT[774007]  # Head and neck structure (body structure)
]

Concept Ancestors: [SNOMEDCT[774007]  # Head and neck structure (body structure)
, SNOMEDCT[70104002]  # Upper body part structure (body structure)
, SNOMEDCT[128262006]  # Upper body structure (body structure)
, SNOMEDCT[38866009]  # Body part structure (body structure)
, SNOMEDCT[52530000]  # Body region structure (body structure)
, SNOMEDCT[91723000]  # Anatomical structure (body structure)
, SNOMEDCT[91722005]  # Physical anatomical entity (body structure)
, SNOMEDCT[257728006]  # Anat

Concept: SNOMEDCT[769395004]  # Thick film dose amount (qualifier value)

Concept Code: 769395004

Concept Name: Thick film dose amount (qualifier value)

Concept Synonyms: ['Thick film', 'Thick film dose amount', 'Thick film dose amount (qualifier value)']

Concept Parents: [SNOMEDCT[769391008]  # Non-numeric dose amount (qualifier value)
]

Concept Ancestors: [SNOMEDCT[769391008]  # Non-numeric dose amount (qualifier value)
, SNOMEDCT[118598001]  # Property of measurement (qualifier value)
, SNOMEDCT[106228007]  # Modifier, linkage term AND/OR qualifier (qualifier value)
, SNOMEDCT[362981000]  # Qualifier value (qualifier value)
, SNOMEDCT[138875005]  # SNOMED CT Concept (SNOMED RT+CTV3)
, SNOMEDCT[370227000]  # Modifier AND/OR qualifier (qualifier value)
]

Concept Children: []

Concept Descendants: []

Concept is Sub-part of: []

Concept is Super-part of: []

All Super-parts of Concept: []

All Sub-parts of Concept: []

concept.relations: set()

concept.groups: []

concept.groups.r

In [12]:
for i in range(0,len(concept_list)-1):
    for j in range(i+1,len(concept_list)):
        try:
            print(f"{concept_list[i]} is a part of {concept_list[j]}: {concept_list[i].is_part_of(concept_list[j])} \n\n")
        except Exception as e:
            continue

SNOMEDCT[157054009]  # Entire subcutaneous tissue of anterior portion of neck (body structure)
 is a part of SNOMEDCT[49928004]  # Structure of anterior portion of neck (body structure)
: True 


SNOMEDCT[157054009]  # Entire subcutaneous tissue of anterior portion of neck (body structure)
 is a part of SNOMEDCT[5751008]  # Subcutaneous tissue structure of anterior portion of neck (body structure)
: True 


SNOMEDCT[157054009]  # Entire subcutaneous tissue of anterior portion of neck (body structure)
 is a part of SNOMEDCT[142006001]  # Entire skeletal muscle of tongue, palate, pharynx AND/OR nose (body structure)
: False 


SNOMEDCT[157054009]  # Entire subcutaneous tissue of anterior portion of neck (body structure)
 is a part of SNOMEDCT[181195007]  # Entire nose (body structure)
: False 


SNOMEDCT[157054009]  # Entire subcutaneous tissue of anterior portion of neck (body structure)
 is a part of SNOMEDCT[181201004]  # [SO]Specified nose NEC (body structure)
: False 


SNOMEDCT[157

SNOMEDCT[244089006]  # Skin of side of nose (body structure)
 is a part of SNOMEDCT[289302005]  # Umbilical cord thick (finding)
: False 


SNOMEDCT[244089006]  # Skin of side of nose (body structure)
 is a part of SNOMEDCT[289584009]  # Lochia thick (finding)
: False 


SNOMEDCT[244089006]  # Skin of side of nose (body structure)
 is a part of SNOMEDCT[289768005]  # Cervix thick (finding)
: False 


SNOMEDCT[244089006]  # Skin of side of nose (body structure)
 is a part of SNOMEDCT[289809006]  # Thick cervical mucous (finding)
: False 


SNOMEDCT[244089006]  # Skin of side of nose (body structure)
 is a part of SNOMEDCT[358912005]  # Thick & Easy (substance)
: False 


SNOMEDCT[244089006]  # Skin of side of nose (body structure)
 is a part of SNOMEDCT[48610005]  # Coarse hair (finding)
: False 


SNOMEDCT[244089006]  # Skin of side of nose (body structure)
 is a part of SNOMEDCT[395413001]  # Adhesive 22.5cmx10cmx5mm thick felt (physical object)
: False 


SNOMEDCT[244089006]  # Skin 

SNOMEDCT[312167001]  # Vein of internal nose (body structure)
 is a part of SNOMEDCT[730349005]  # Entire embryonic pharyngeal pouch (body structure)
: False 


SNOMEDCT[312167001]  # Vein of internal nose (body structure)
 is a part of SNOMEDCT[56411004]  # Entire Waldeyer's ring (body structure)
: False 


SNOMEDCT[312167001]  # Vein of internal nose (body structure)
 is a part of SNOMEDCT[17861009]  # Waldeyer's ring structure (body structure)
: False 


SNOMEDCT[312167001]  # Vein of internal nose (body structure)
 is a part of SNOMEDCT[1260258006]  # Structure of pharyngeal branch of descending palatine artery (body structure)
: False 


SNOMEDCT[312167001]  # Vein of internal nose (body structure)
 is a part of SNOMEDCT[1260261007]  # Entire pharyngeal branch of descending palatine artery (body structure)
: False 


SNOMEDCT[312167001]  # Vein of internal nose (body structure)
 is a part of SNOMEDCT[264231000]  # Entire throat (surface region of neck) (body structure)
: False 




SNOMEDCT[361926005]  # Entire apex of nose (body structure)
 is a part of SNOMEDCT[425078002]  # Genus Burhinus (organism)
: False 


SNOMEDCT[361926005]  # Entire apex of nose (body structure)
 is a part of SNOMEDCT[425252002]  # Burhinus superciliaris (organism)
: False 


SNOMEDCT[361926005]  # Entire apex of nose (body structure)
 is a part of SNOMEDCT[423122002]  # Burhinus bistriatus (organism)
: False 


SNOMEDCT[361926005]  # Entire apex of nose (body structure)
 is a part of SNOMEDCT[424488003]  # Burhinus grallarius (organism)
: False 


SNOMEDCT[361926005]  # Entire apex of nose (body structure)
 is a part of SNOMEDCT[424326001]  # Burhinus giganteus (organism)
: False 


SNOMEDCT[361926005]  # Entire apex of nose (body structure)
 is a part of SNOMEDCT[423283000]  # Burhinus oedicnemus (organism)
: False 


SNOMEDCT[361926005]  # Entire apex of nose (body structure)
 is a part of SNOMEDCT[423510008]  # Burhinus vermiculatus (organism)
: False 


SNOMEDCT[361926005]  # Entir

SNOMEDCT[368114008]  # Entire dorsum of nose (body structure)
 is a part of SNOMEDCT[139887008]  # Patient: [condition improved] or [better] or [very much better]
: False 


SNOMEDCT[368114008]  # Entire dorsum of nose (body structure)
 is a part of SNOMEDCT[139893000]  # Patient condition: [poor] or [unstable]
: False 


SNOMEDCT[368114008]  # Entire dorsum of nose (body structure)
 is a part of SNOMEDCT[152414009]  # Removed patients request: [FP22] or [GP22]
: False 


SNOMEDCT[368114008]  # Entire dorsum of nose (body structure)
 is a part of SNOMEDCT[157852007]  # Medical accidents to patients during surgical and medical care
: False 


SNOMEDCT[368114008]  # Entire dorsum of nose (body structure)
 is a part of SNOMEDCT[184191002]  # Removed patients request: [FP22] or [GP22]
: False 


SNOMEDCT[368114008]  # Entire dorsum of nose (body structure)
 is a part of SNOMEDCT[216870003]  # Accidents to patients during care: (& [surgical] or [medical])
: False 


SNOMEDCT[368114008]  # E


SNOMEDCT[400041007]  # Entire skin of supratip of nose (body structure)
 is a part of SNOMEDCT[402006001]  # Ring polythene pessary 7.5mm thick, 62mm diameter (physical object)
: False 


SNOMEDCT[400041007]  # Entire skin of supratip of nose (body structure)
 is a part of SNOMEDCT[402007005]  # Ring polythene pessary 7.5mm thick, 65mm diameter (physical object)
: False 


SNOMEDCT[400041007]  # Entire skin of supratip of nose (body structure)
 is a part of SNOMEDCT[402008000]  # Ring polythene pessary 7.5mm thick, 68mm diameter (physical object)
: False 


SNOMEDCT[400041007]  # Entire skin of supratip of nose (body structure)
 is a part of SNOMEDCT[402009008]  # Ring polythene pessary 7.5mm thick, 71mm diameter (physical object)
: False 


SNOMEDCT[400041007]  # Entire skin of supratip of nose (body structure)
 is a part of SNOMEDCT[402010003]  # Ring polythene pessary 7.5mm thick, 74mm diameter (physical object)
: False 


SNOMEDCT[400041007]  # Entire skin of supratip of nose (bod

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=2000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



SNOMEDCT[396855009]  # Rhynchopsitta pachyrhyncha (organism)
 is a part of SNOMEDCT[408195004]  # Thick film for malarial parasites (procedure)
: False 


SNOMEDCT[396855009]  # Rhynchopsitta pachyrhyncha (organism)
 is a part of SNOMEDCT[107089003]  # Family burhinidae (organism)
: False 


SNOMEDCT[396855009]  # Rhynchopsitta pachyrhyncha (organism)
 is a part of SNOMEDCT[425078002]  # Genus Burhinus (organism)
: False 


SNOMEDCT[396855009]  # Rhynchopsitta pachyrhyncha (organism)
 is a part of SNOMEDCT[425252002]  # Burhinus superciliaris (organism)
: False 


SNOMEDCT[396855009]  # Rhynchopsitta pachyrhyncha (organism)
 is a part of SNOMEDCT[423122002]  # Burhinus bistriatus (organism)
: False 


SNOMEDCT[396855009]  # Rhynchopsitta pachyrhyncha (organism)
 is a part of SNOMEDCT[424488003]  # Burhinus grallarius (organism)
: False 


SNOMEDCT[396855009]  # Rhynchopsitta pachyrhyncha (organism)
 is a part of SNOMEDCT[424326001]  # Burhinus giganteus (organism)
: False 


SNOMEDCT[3